## ELEX 4653 Final Exam

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

Define a function `lslen(l)`
that is passed a list of strings.  The function should return a list containing 
the length of
each item in `l`.

For example `lslen(["a", "abc", ""])` would return `[1,3,0]`.

#### Question 2

Define a function `chrset(s)`
that is passed a string `s`.
The function should return a set containing each character of the string `s`.

For example, `chrset("aabc")` would return `{'a', 'b', 'c'}`.



#### Question 3

Declare a class named 
`upcnt`
whose constructor (`__init__(self)`) takes no other arguments and contains one member function named `next()` that returns
the next in a sequence of integer values that increase by one, starting with zero.

For example:
```
o = upcnt()
print(o.next(), o.next())
```
would print `0 1`.



#### Question 4

Write a function `converta(l)` that takes a list of strings `l` and returns another list 
containing only the strings that are composed entirely of upper-case characters.

For example, `converta(['aBc', '123', 'A B', 'ABC'])` would return
`['A B', 'ABC']`.



#### Question 5

Define a string named `myrea` containing a regular expression that matches a string
starting with a vowel (a,e,i,o, or u), followed by a hyphen (-), followed by the any of the letters P or Q repeated 2 or 3 times.

For example, it would match: 'a-PQx', 'u-PPP ' or 'i-PQQ'
but not 'x-PQx', 'u=PPP ' or 'i-P'.



In [25]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    import traceback
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.search(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.search(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o
    
    import math
    def roundn(num, n):
        return 0 if not num else round(num, -int(math.floor(math.log10(abs(num)))) + (n - 1))

    def ch(s,n=(1,1)):
        return randwords(1,chars=s,nl=n)[0]
        
    def Q1():
        f,a = lslen,randwords(randint(3,5)) 
        oa = copy.deepcopy(a)
        r = f(a)
        return r,f"{f.__name__}({repr(oa)}) returns {r}"  
    
    def Q2():
        f,a = chrset,randwords(1,nl=(6,9))[0]
        oa = copy.deepcopy(a)
        r = f(a)
        return r,f"{f.__name__}({repr(oa)}) returns {r}"
    
    def Q3():
        o = upcnt()
        r = [roundn(o.next(),4) for i in range(randint(5,9))]       
        return r,f"next() returns {r}"
    
    def Q4():
        f,a = converta,randwords(randint(4,6),chars="ABCDEFGhij") 
        oa = copy.deepcopy(a)
        r = f(a)
        return r,f"{f.__name__}({repr(oa)}) returns {r}"
    
    def Q5():
        l = string.ascii_lowercase
        a = ( (f"{ch('aeiou',(1,1))}-{''.join(randwords(1,chars='PQ',nl=(2,3)))}{ch(' xyz',(0,1))}",), 
              (f"{ch('xyz ',(1,3))}{ch('aeiou',(1,1))}{ch('PQ',(2,3))}{randwords(1,nl=(0,1))[0]}",) )
        checkre(myrea,*a)
        return 0,0

    hashvalues = '''
y+HoW3noUWbryLPNoOfK+F1mcJGcJGWiKJCvL8GT
YJiQU7CFy0zyvRBbNGPMvjmaliFTJTUWWl6MVul/
RpvQ6w680IlDRpvQ0IlDRpvQG9/w0IlDRpvQG9/w
uq5HsQSmq1ESq1ESjEZ37s9Zq1ESjg4nq1ESq1ES
qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                #traceback.print_exc()
                err = f"Error during test {n}: {e}"               
        if testing:
            newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)